This file is used to process the bacteria information from the different websites, then it merges it with the existing dataframe that stores the RNA information.

Relevant Links: 
* ncbi archae: https://ftp.ncbi.nlm.nih.gov/genomes/refseq/archaea/
* ncbi bacteria: https://ftp.ncbi.nlm.nih.gov/genomes/refseq/bacteria/
* progenome: https://progenomes.embl.de/download.cgi

In [1]:
# Import statements
import os
from ftplib import FTP
import pandas as pd
import numpy as np
import os
from Bio import SeqIO
import gzip
import shutil
import pickle
import sys

## Get Taxon_ID and bacterium name

In [2]:
df = pd.read_csv("data/superkingdom2descendents.csv").loc[:, ['taxon_id', 'scientific_name', 'superkingdom']]
print(df['superkingdom'].unique())
df_bacteria_taxon = df.loc[df['superkingdom'].isin(['Eukaryota','Bacteria','Archaea'])]
print(df_bacteria_taxon['superkingdom'].unique())
print(df_bacteria_taxon)

['Eukaryota' 'Bacteria' 'Archaea' 'Viruses' 'Viroids']
['Eukaryota' 'Bacteria' 'Archaea']
         taxon_id            scientific_name superkingdom
0             127               Mus musculus    Eukaryota
1             129                   Bacteria     Bacteria
2             130               Azorhizobium     Bacteria
3             131   Azorhizobium caulinodans     Bacteria
4             132        Buchnera aphidicola     Bacteria
...           ...                        ...          ...
1485563   1495800                 Boragineae    Eukaryota
1485564   1495801     Synthetonychia proxima    Eukaryota
1485565   1495802  Pseudoalteromonas sp. BMB     Bacteria
1485566   1495803               Panacibacter     Bacteria
1485567   1495804            Lipingzhangella     Bacteria

[1325218 rows x 3 columns]


## Get Archaea and Bacteria Donwload Paths

In [29]:
# Get info about the archae
# https://ftp.ncbi.nlm.nih.gov/genomes/refseq/archaea/
bacteria_paths = []
ftp = FTP('ftp.ncbi.nlm.nih.gov')
ftp.login()
ftp.cwd('genomes/refseq/archaea/')
directories = ftp.nlst() # Get all of the types of archae
print(len(directories))
ftp.close()

1219


In [30]:
directory = '~/genomes/refseq/archaea/'
for index, row in df_bacteria_taxon.iterrows():
    if index % 10000 == 0:
        print(index)
    name = row['scientific_name'].replace(" ", "_")
    arr = [row['taxon_id'],[]]
    if (name in directories):
        ftp = FTP('ftp.ncbi.nlm.nih.gov')
        ftp.login()
        new_directory:str = directory + name + '/all_assembly_versions/'
        ftp.cwd(new_directory)
        try:  
            if 'suppressed' in ftp.nlst():
                ftp.cwd('suppressed/')
                new_directory += 'suppressed/'
            for d in ftp.nlst():
              arr[1].append(new_directory + d + '/' )
        except EOFError as e:
            print(e)
        bacteria_paths.append(arr)
        ftp.close()

0
10000
20000
30000
50000
60000
70000
80000
90000
100000
120000
130000
140000
150000
160000
170000
180000
190000
200000
210000
220000
230000
240000
250000
260000
270000
290000
300000
320000
330000
340000
350000
360000
380000
390000
400000
410000
420000
430000
440000
450000
460000
480000
490000
500000
510000
520000
530000
540000
550000
560000
570000
590000
610000
620000
630000
640000
650000
660000
680000
690000
700000
710000
720000
730000
740000
760000
770000
780000
800000
810000
820000
850000
860000
870000
890000
910000
920000
950000
960000
970000
980000
990000
1000000
1010000
1020000
1030000
1040000
1050000
1060000
1070000
1090000
1100000
1110000
1120000
1130000
1140000
1150000
1160000
1170000
1180000
1190000
1200000
1210000
1220000
1230000
1240000
1260000
1270000
1280000
1290000
1300000
1310000
1320000
1330000
1340000
1350000
1360000
1370000
1390000
1410000
1420000
1440000
1460000
1470000
1480000


In [33]:
ftp.close()
print(len(bacteria_paths))
print(bacteria_paths[0])

650
[1834, ['~/genomes/refseq/archaea/Methanobacterium_bryantii/all_assembly_versions/GCF_002287175.1_ASM228717v1/']]


In [34]:
with open("archaea_paths_only", "wb") as fp: #pickling
    pickle.dump(bacteria_paths, fp)

In [6]:
# Now do the same and get the directory names for all of the bacteria
directory = '~/genomes/refseq/bacteria/'
# Get the list of all directories again 
ftp = FTP('ftp.ncbi.nlm.nih.gov')
ftp.login()
ftp.cwd(directory)
directories = ftp.nlst()
ftp.close()
bacteria_paths = pd.read_pickle("archaea_paths_only")
for index, row in df_bacteria_taxon.iterrows():
    name = row['scientific_name'].replace(" ", "_")
    arr = [row['taxon_id'],[]]
    if (name in directories):
        ftp = FTP('ftp.ncbi.nlm.nih.gov')
        ftp.login()
        new_directory:str = directory + name + '/all_assembly_versions/'
        ftp.cwd(new_directory)
        try:  
            list = ftp.nlst()
            if 'suppressed' in list:
                ftp.cwd('suppressed/')
                new_directory += 'suppressed/'
            list = ftp.nlst()
            for d in list:
              arr[1].append(new_directory + d + '/' )
        except EOFError as e:
            print(e)
        bacteria_paths.append(arr)
        ftp.close()
    if index % 10000 == 0:
        print(len(bacteria_paths))

['Abditibacterium_utsteinense', 'Abiotrophia_defectiva', 'Abiotrophia_sp._HMSC24B09', 'Absicoccus_porci', 'Absiella_sp._AM09-45', 'Absiella_sp._AM09-50', 'Absiella_sp._AM10-20', 'Absiella_sp._AM22-9', 'Absiella_sp._AM27-20', 'Absiella_sp._AM29-15', 'Absiella_sp._AM54-8XD', 'Abyssibacter_profundi', 'Abyssicoccus_albus', 'Abyssisolibacter_fermentans', 'Abyssogena_phaseoliformis_symbiont', 'Acanthopleuribacter_pedis', 'Acaricomes_phytoseiuli', 'Acaryochloris_marina', 'Acaryochloris_sp._CCMEE_5410', 'Georgenia_sp._TF02-10', 'Acerihabitans_arboris', 'Acetanaerobacterium_elongatum', 'Acetanaerobacterium_sp._MSJ-12', 'Acetatifactor_muris', 'Acetilactobacillus_jinshanensis', 'Acetitomaculum_ruminis', 'Acetivibrio_alkalicellulosi', 'Acetivibrio_cellulolyticus', 'Acetivibrio_clariflavus', 'Acetivibrio_ethanolgignens', 'Acetobacter_lambici', 'Acetivibrio_mesophilus', 'Acetivibrio_saccincola', 'Acetivibrio_sp._MSJd-27', 'Acetivibrio_straminisolvens', 'Acetivibrio_thermocellus', 'Acetoanaerobium_no

[131, ['~/genomes/refseq/bacteria/Azorhizobium_caulinodans/all_assembly_versions/GCF_000010525.1_ASM1052v1/']]
[132, ['~/genomes/refseq/bacteria/Buchnera_aphidicola/all_assembly_versions/suppressed/GCF_000183245.1_ASM18324v1/', '~/genomes/refseq/bacteria/Buchnera_aphidicola/all_assembly_versions/suppressed/GCF_000183305.1_ASM18330v1/', '~/genomes/refseq/bacteria/Buchnera_aphidicola/all_assembly_versions/suppressed/GCF_005080785.1_ASM508078v1/', '~/genomes/refseq/bacteria/Buchnera_aphidicola/all_assembly_versions/suppressed/GCF_026122835.1_ASM2612283v1/']]
[134, ['~/genomes/refseq/bacteria/Cellulomonas_gilvus/all_assembly_versions/GCF_000218545.1_ASM21854v1/']]
[136, ['~/genomes/refseq/bacteria/Dictyoglomus_thermophilum/all_assembly_versions/GCF_000020965.1_ASM2096v1/', '~/genomes/refseq/bacteria/Dictyoglomus_thermophilum/all_assembly_versions/GCF_008244535.1_ASM824453v1/', '~/genomes/refseq/bacteria/Dictyoglomus_thermophilum/all_assembly_versions/GCF_026418735.1_ASM2641873v1/']]
[138, 

[184, ['~/genomes/refseq/bacteria/Simonsiella_muelleri/all_assembly_versions/GCF_000163775.1_ASM16377v1/', '~/genomes/refseq/bacteria/Simonsiella_muelleri/all_assembly_versions/GCF_000163775.2_Simo_muel_ATCC_29453_V2/', '~/genomes/refseq/bacteria/Simonsiella_muelleri/all_assembly_versions/GCF_002951835.1_ASM295183v1/', '~/genomes/refseq/bacteria/Simonsiella_muelleri/all_assembly_versions/GCF_020162275.1_ASM2016227v1/', '~/genomes/refseq/bacteria/Simonsiella_muelleri/all_assembly_versions/GCF_937989625.1_SRR8114033_bin.4_CONCOCT_v1.1_MAG/', '~/genomes/refseq/bacteria/Simonsiella_muelleri/all_assembly_versions/GCF_963520605.1_ERR9969030_bin.13_MetaWRAP_v1.3_MAG/']]
[186, ['~/genomes/refseq/bacteria/Caulobacter_sp./all_assembly_versions/GCF_017418455.1_ASM1741845v1/', '~/genomes/refseq/bacteria/Caulobacter_sp./all_assembly_versions/GCF_017744445.1_ASM1774444v1/']]
[188, ['~/genomes/refseq/bacteria/Hyphomicrobium_sp./all_assembly_versions/GCF_003987725.1_ASM398772v1/', '~/genomes/refseq/ba

[234, ['~/genomes/refseq/bacteria/Borrelia_hermsii/all_assembly_versions/GCF_000012065.1_ASM1206v1/', '~/genomes/refseq/bacteria/Borrelia_hermsii/all_assembly_versions/GCF_000012065.2_ASM1206v2/', '~/genomes/refseq/bacteria/Borrelia_hermsii/all_assembly_versions/GCF_000568675.1_ASM56867v1/', '~/genomes/refseq/bacteria/Borrelia_hermsii/all_assembly_versions/GCF_000568775.1_ASM56877v1/', '~/genomes/refseq/bacteria/Borrelia_hermsii/all_assembly_versions/GCF_000568795.1_ASM56879v1/', '~/genomes/refseq/bacteria/Borrelia_hermsii/all_assembly_versions/GCF_000956315.1_ASM95631v1/', '~/genomes/refseq/bacteria/Borrelia_hermsii/all_assembly_versions/GCF_001598195.1_ASM159819v1/', '~/genomes/refseq/bacteria/Borrelia_hermsii/all_assembly_versions/GCF_001660005.1_ASM166000v1/', '~/genomes/refseq/bacteria/Borrelia_hermsii/all_assembly_versions/GCF_020422925.1_ASM2042292v1/', '~/genomes/refseq/bacteria/Borrelia_hermsii/all_assembly_versions/GCF_020865525.1_ASM2086552v1/', '~/genomes/refseq/bacteria/Bo

[255, ['~/genomes/refseq/bacteria/Treponema_bryantii/all_assembly_versions/GCF_000421345.1_ASM42134v1/', '~/genomes/refseq/bacteria/Treponema_bryantii/all_assembly_versions/GCF_900111035.1_IMG-taxon_2623620477_annotated_assembly/', '~/genomes/refseq/bacteria/Treponema_bryantii/all_assembly_versions/GCF_900113965.1_IMG-taxon_2606217736_annotated_assembly/']]
[256, ['~/genomes/refseq/bacteria/Treponema_pectinovorum/all_assembly_versions/GCF_900497565.1_PRJEB27758/', '~/genomes/refseq/bacteria/Treponema_pectinovorum/all_assembly_versions/GCF_900497585.1_PRJEB27761/', '~/genomes/refseq/bacteria/Treponema_pectinovorum/all_assembly_versions/GCF_900497595.1_PRJEB27760/', '~/genomes/refseq/bacteria/Treponema_pectinovorum/all_assembly_versions/GCF_900566195.1_PRJEB27756/', '~/genomes/refseq/bacteria/Treponema_pectinovorum/all_assembly_versions/GCF_900573895.1_PRJEB29053/']]
[257, ['~/genomes/refseq/bacteria/Treponema_saccharophilum/all_assembly_versions/GCF_000255555.1_ASM25555v2/']]
[258, ['~/

...

[1012349, ['~/genomes/refseq/bacteria/Actinoplanes_sp._ATCC_53533/all_assembly_versions/GCF_003947245.1_ASM394724v1/']]
[1012361, ['~/genomes/refseq/bacteria/Yersinia_pekkanenii/all_assembly_versions/GCF_001152565.1_4821_6_12/', '~/genomes/refseq/bacteria/Yersinia_pekkanenii/all_assembly_versions/GCF_001244635.1_8016_2_92/']]
[1012365, ['~/genomes/refseq/bacteria/Actinomyces_timonensis/all_assembly_versions/GCF_000295095.1_ASM29509v1/']]
[1012366, ['~/genomes/refseq/bacteria/Moraxella_porci/all_assembly_versions/GCF_002014855.1_ASM201485v1/', '~/genomes/refseq/bacteria/Moraxella_porci/all_assembly_versions/GCF_029845525.1_ASM2984552v1/']]
[1012367, ['~/genomes/refseq/bacteria/Corynebacterium_pilbarense/all_assembly_versions/GCF_026930265.1_ASM2693026v1/']]
[1012383, ['~/genomes/refseq/bacteria/Pseudomonas_guariconensis/all_assembly_versions/GCF_002864765.1_ASM286476v1/', '~/genomes/refseq/bacteria/Pseudomonas_guariconensis/all_assembly_versions/GCF_002864815.1_ASM286481v1/', '~/genomes

[1018845, ['~/genomes/refseq/bacteria/Mucilaginibacter_yixingensis/all_assembly_versions/GCF_003050755.1_ASM305075v1/']]
[1018858, ['~/genomes/refseq/bacteria/Cellulomonas_sp._B6/all_assembly_versions/GCF_001462455.1_ASM146245v1/']]
[1019475, ['~/genomes/refseq/bacteria/Anabaena_catenula/all_assembly_versions/GCF_014698735.1_ASM1469873v1/']]
[1019563, ['~/genomes/refseq/bacteria/Aquimarina_pacifica/all_assembly_versions/GCF_000520955.1_of_Aquimarina_pacifica/']]
[1019685, ['~/genomes/refseq/bacteria/Enterococcus_xiangfangensis/all_assembly_versions/GCF_005405365.1_ASM540536v1/', '~/genomes/refseq/bacteria/Enterococcus_xiangfangensis/all_assembly_versions/GCF_016909115.1_ASM1690911v1/', '~/genomes/refseq/bacteria/Enterococcus_xiangfangensis/all_assembly_versions/GCF_031928845.1_ASM3192884v1/']]
[1019713, ['~/genomes/refseq/bacteria/Geodermatophilus_amargosae/all_assembly_versions/GCF_900116515.1_IMG-taxon_2599185195_annotated_assembly/']]
[1019814, ['~/genomes/refseq/bacteria/Aquabacter

[1021789, ['~/genomes/refseq/bacteria/Flavobacterium_urocaniciphilum/all_assembly_versions/GCF_900110615.1_IMG-taxon_2693429864_annotated_assembly/']]
[1021916, ['~/genomes/refseq/bacteria/Enterobacter_sp._C6/all_assembly_versions/GCF_008122455.1_ASM812245v1/']]
[1022166, ['~/genomes/refseq/bacteria/Bradyrhizobium_retamae/all_assembly_versions/GCF_001440415.1_ASM144041v1/']]
[1022367, ['~/genomes/refseq/bacteria/Streptomyces_zhaozhouensis/all_assembly_versions/GCF_900230195.1_IMG-taxon_2718217652_annotated_assembly/']]
[1022371, ['~/genomes/refseq/bacteria/Mesorhizobium_kowhaii/all_assembly_versions/GCF_003253745.1_ASM325374v1/']]
[1022375, ['~/genomes/refseq/bacteria/Mesorhizobium_sophorae/all_assembly_versions/GCF_002270415.1_ASM227041v1/']]
[1022380, ['~/genomes/refseq/bacteria/Mesorhizobium_waimense/all_assembly_versions/GCF_003601975.1_ASM360197v1/']]
[1022972, ['~/genomes/refseq/bacteria/Mucilaginibacter_sp._PAMC_26640/all_assembly_versions/suppressed/GCF_001596135.1_ASM159613v1/

[1027536, ['~/genomes/refseq/bacteria/Streptomyces_sp._Amel2xB2/all_assembly_versions/GCF_003259355.1_ASM325935v1/']]
[1027537, ['~/genomes/refseq/bacteria/Streptomyces_sp._PsTaAH-137/all_assembly_versions/GCF_003259365.1_ASM325936v1/']]
[1027539, ['~/genomes/refseq/bacteria/Streptomyces_sp._DpondAA-E10/all_assembly_versions/GCF_003259275.1_ASM325927v1/']]
[1027541, ['~/genomes/refseq/bacteria/Rhodococcus_sp._JG-3/all_assembly_versions/GCF_000482405.1_ASM48240v1/']]
[1027542, ['~/genomes/refseq/bacteria/Sporosarcina_sp._EUR3_2.2.2/all_assembly_versions/suppressed/GCF_000484595.1_ASM48459v1/']]
[1027543, ['~/genomes/refseq/bacteria/Streptomyces_sp._CNS606/all_assembly_versions/suppressed/GCF_000426325.1_ASM42632v1/']]
[1027544, ['~/genomes/refseq/bacteria/Streptomyces_sp._KhCrAH-40/all_assembly_versions/suppressed/GCF_000514095.1_ASM51409v1/']]
[1027545, ['~/genomes/refseq/bacteria/Streptomyces_sp._KhCrAH-337/all_assembly_versions/suppressed/GCF_000514075.1_ASM51407v1/']]
[1027834, ['~/

TimeoutError: [WinError 10060] A connection attempt failed because the connected party did not properly respond after a period of time, or established connection failed because connected host has failed to respond

In [14]:
# save the name of all of the ncbi directories
with open("bacteria_paths", "wb") as fp: #pickling
    pickle.dump(bacteria_paths, fp)
    
b = pd.read_pickle("bacteria_paths")
print(b[0])

[1834, ['~/genomes/refseq/archaea/Methanobacterium_bryantii/all_assembly_versions/GCF_002287175.1_ASM228717v1/']]


In [33]:
# Now I will take the original data that I got and figure out how many genetic sequences
# I need to store per bacterium. This will later be used so that I don't need to iterate
df_phage_seqs = pd.read_pickle("df_bacteria_phageseq.pkl")
print(df_phage_seqs.columns)
taxid_count = dict()

for tax_id in :
    taxid_count.update({int(tax_id) : len(df_phage_seqs[df_phage_seqs['host_taxon_id'] == tax_id])})
print(taxid_count)

Index(['host_taxon_id', 'viral_cluster_id', 'seq_str'], dtype='object')
{24: 1, 52: 1, 75: 5, 192: 2, 194: 5, 205: 2, 197: 20, 195: 9, 887301: 2, 887309: 1, 887310: 1, 889224: 1, 889236: 1, 889244: 1, 889250: 1, 889216: 1, 199: 1, 210: 1, 235: 1, 29459: 1, 29461: 1, 36855: 1, 204722: 1, 262698: 1, 359391: 1, 430066: 1, 483179: 1, 520450: 1, 520454: 1, 520455: 1, 520461: 1, 520466: 1, 520487: 1, 546272: 1, 568815: 1, 703352: 1, 941967: 1, 981386: 3, 1004954: 1, 1104320: 1, 1104321: 1, 1112912: 1, 1210454: 1, 1885919: 3, 1891098: 1, 239: 1, 264: 2, 270: 4, 274: 3, 286: 25, 287: 184, 1402507: 2, 350703: 2, 1333855: 6, 686340: 4, 1279007: 5, 1009714: 6, 208963: 4, 1402544: 1, 652611: 5, 1340851: 2, 1427342: 6, 1093787: 1, 381754: 7, 1123015: 2, 1402522: 1, 1402504: 3, 1415629: 5, 1279008: 4, 1198629: 2, 1402563: 3, 1400868: 9, 1434267: 12, 1402577: 3, 1193501: 2, 1402494: 7, 1286151: 2, 1306165: 1, 1402505: 3, 1402524: 2, 1411701: 8, 1051003: 3, 1051004: 3, 1051005: 3, 1402564: 3, 1408193:

In [ ]:
bacteria_paths = pd.read_pickle("bacteria_paths")
bacteria_transcripts = dict()
for bac in bacteria_paths:
    tax_id = bac[0]
    filename = ""
    # Extract file
    for path in bac[1]:
        if '.txt' in path:
            print(path)
            continue
        split_path = path.rsplit('/')
        filename = split_path[len(split_path) - 2] + '_genomic.fna.gz'
        # Get .gz file
        ftp = FTP('ftp.ncbi.nlm.nih.gov')
        ftp.login()
        ftp.cwd(path)
        f = open(filename, 'wb')
        try :   
            if filename in ftp.nlst():
                ftp.retrbinary(f"RETR {filename}", f.write)
                f.close()
                ftp.close()
                break
            else:
                filename = ""
                f.close()
                ftp.close()
                continue
        except:
            filename = ""
            f.close()
            ftp.close()
    if not filename:
        print(filename)
        print("failed to get file")
        continue
    # Unzip .gz file
    dest_file = 'dest_file.fna'
    with gzip.open(filename, 'rb') as f_in:
        with open(dest_file, 'wb') as f_out:
            shutil.copyfileobj(f_in, f_out)
    # Extract as many sequences from the file as needed
    arr = []
    for fasta in SeqIO.parse(open(dest_file), 'fasta'):
        arr.append(str(fasta.seq))
    if len(bacteria_transcripts) % 1000 == 0:
        print(tax_id)
    bacteria_transcripts.update({tax_id : arr})
    # Remove files when done for cleaning
    f_in.close()
    f_out.close()
    os.remove(dest_file)

1834

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file
~/genomes/refseq/bacteria/Campylobacter_coli/all_assembly_versions/README.txt/

failed to get file
~/genomes/refseq/bacteria/Campylobacter_jejuni/all_assembly_versions/README.txt/

failed to get file
~/genomes/refseq/bacteria/Helicobacter_pylori/all_assembly_versions/README.txt/

failed to get file

failed to get file
~/genomes/refseq/bacteria/Pseudomonas_aeruginosa/all_assembly_versions/README.txt/

failed to g


failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file
795185

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to get file

failed to ge

In [ ]:
with open("bacteria_transcripts.pckl", "wb") as fp: #pickling
    pickle.dump(bacteria_transcripts, fp)

In [ ]:
print(len(bacteria_transcripts))

Finally, iterate through all of the phage sequences and map each to a bacteria sequence, and add this to a new data frame. We can now use this data frame for our experiments :D 